In [1]:
import numpy as np
import pandas as pd

import sklearn.neighbors as neighbors

from importlib import reload
import copy
import synthetic.render.generator as gen

import matplotlib.pyplot as plt
import matplotlib as mpl
%matplotlib inline

import multiprocessing as mp

import sys
import os
import math
import logging
import time
import galsim
import fitsio as fio

import ngmix

import synthetic.render.render as render
import synthetic.render.icl as icl
import images
import subprocess

In [2]:
catalog_path = '/e/ocean1/users/vargatn/DES/SIM_DATA/SKY_MODEL_EPSILON/res_clust_v2_z0l0/epsilon_clust_v8-z0l0_15000_000.fits'
data = fio.read(catalog_path)
catalog_cluster = data[data['LOC'] == 1]
catalog_field = data[data['LOC'] == 0]

In [3]:
catalog = np.hstack((catalog_cluster, catalog_field))
catalog = np.hstack((catalog_cluster, catalog_field))
catalog['G1'] = 0.3
catalog['G2'] = -0.2

In [4]:
class Shear(object):
    def __init__(self, canvas, image_epsf, maskmap):
        self.canvas = canvas.copy()
        self.image_epsf = image_epsf
        self.BADVAL = -9999
        self.maskmap = galsim.ImageI(maskmap).copy()
        
    def extract_stamps(self, centers, imasks, sizes):
                
        self.stamps = []
        self.masks = []
        for i in np.arange(len(centers)):
            half_size = sizes[i] // 2 + 2
            cen = centers[i]
            bb = galsim.bounds.BoundsI(np.round(cen[0]) - half_size,
                                       np.round(cen[0]) + half_size - 1,
                                       np.round(cen[1]) - half_size,
                                       np.round(cen[1]) + half_size - 1)
#             print(bb, half_size)
            stamp = self.canvas[bb].array.copy()
            mask = self.maskmap[bb].array.copy()
#             mm = (mask.array != imasks[i]) & (mask.array != 0)
            mm = (mask != imasks[i]) & (mask != 0)
            muniques = np.unique(mask)
#             print(np.unique(mask), imasks[i], bb)
            stamp[mm] = 0
            mask[mm] = 0
#             
            self.masks.append(self.maskmap[bb].array.copy())
            self.stamps.append(galsim.ImageF(stamp))


    def estimate_shear(self, sky_var=0, shear_est="KSB", which="canvas"):
        """
        shear modes = REGAUSS’, ‘LINEAR’, ‘BJ’, or ‘KSB’
        which is raw or canvas, default to canvas
        """
        
#         stamps = self.raw_stamps
        if which == "canvas":
            stamps = self.stamps
        
        self.logs = []
        self.shears = []
        self.success = []
        self.fluxes = []
        self.shears_error = []
        for i, im in enumerate(stamps):
            try:
                res = galsim.hsm.EstimateShear(im, self.image_epsf, shear_est=shear_est, sky_var=sky_var)
                self.logs.append(res)
                self.success.append(True)

                tmp = np.array([res.corrected_g1, res.corrected_g2])
                
                self.shears.append(tmp)
                self.fluxes.append(res.moments_amp * (0.27)**2)
                self.shears_error.append(res.corrected_shape_err)
#                 print("here")
            except:
                self.success.append(False)
                self.logs.append(None)
                self.fluxes.append(None)
                tmp = np.array([self.BADVAL, self.BADVAL])
                self.shears.append(tmp)
                self.shears_error.append(None)
                
                
               
        self.fluxes = np.array(self.fluxes)
        self.shears = np.array(self.shears)
        self.success = np.array(self.success)
        self.shears_error = np.array(self.shears_error)



In [9]:
class Frame(object):
    def __init__(self, catalog, name="canvas", canvas_size=5000, band="i", noise_std=8.36, config_se="config.sex"):
        self.catalog = catalog
        self.canvas_size = canvas_size
        self.band = band
        self.noise_std = noise_std
        self.name = name
        self.config_se = config_se
        
    def render(self, nprocess=100):
        self.df = render.DrawField(self.canvas_size, self.catalog, band=self.band)
        self.df.prepare()
        self.df.make_infodicts()
        self.df.multi_render(nprocess)
        self.df.collate_stamps()
        self.canvas = self.df.canvas
        
        self.noise = np.random.normal(scale=self.noise_std, size=(self.canvas_size, self.canvas_size))
        self.canvas += noise
        
        self.write()
        
    def write(self):
        self.file_name = self.name + ".fits"
        fio.write(self.file_name, self.canvas.array, clobber=True)
        self.file_name_psf = self.name + "_epsf.fits"
        fio.write(self.file_name_psf, self.df.image_epsf.array, clobber=True)
        
    def extract(self):
        
        self.file_name = self.name + ".fits"
        self.catalog_name = self.name + "_cat.fits"
        self.seg_name = self.name + "_seg.fits"
        
        cmd = "sex " + self.name + ".fits -c " + self.config_se + " -CATALOG_NAME " + self.catalog_name + " -CHECKIMAGE_NAME " + self.seg_name
        pp = subprocess.Popen(cmd.split(" "), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        out, err = pp.communicate()        
        
        self.scat = fio.read(self.catalog_name)
        self.seg = fio.read(self.seg_name)
        
        
        
    def ksb(self):
        self.file_name = self.name + ".fits"
        self.catalog_name = self.name + "_cat.fits"
        self.seg_name = self.name + "_seg.fits"
        
        self.scat = fio.read(self.catalog_name)
        self.seg = fio.read(self.seg_name)
        self.file_name_psf = self.name + "_epsf.fits"
        self.epsf = fio.read(self.file_name_psf)
        
        canvas = fio.read(self.file_name)
        self.canvas = galsim.ImageF(canvas)
                
        ids = self.scat['NUMBER']
        cens = np.vstack((self.scat['X_IMAGE'], self.scat['Y_IMAGE'])).T
        sizes = np.around(self.scat["FWHM_IMAGE"] * 3)
        self.sc = Shear(self.canvas, self.epsf, self.seg)
        self.sc.extract_stamps(cens, imasks=ids, sizes=sizes)
        self.sc.estimate_shear(sky_var=self.noise_std**2)
        
    

In [10]:
frame = Frame(catalog)

In [11]:
frame.ksb()

In [13]:
frame.sc.stamps

[galsim.Image(bounds=galsim.BoundsI(xmin=1, xmax=18, ymin=1, ymax=18), array=
 array([[-1.94762850e+00, -6.97802305e+00, -4.27288580e+00,
          1.97900715e+01,  2.74867439e+00, -3.07209206e+00,
          1.69667280e+00, -5.26070356e+00, -7.43923855e+00,
          7.13073540e+00, -8.14650726e+00,  4.55965064e-02,
         -8.79412270e+00, -4.56328487e+00,  6.52452374e+00,
          1.33282375e+01, -1.19709387e+01,  1.27531061e+01],
        [-2.63970065e+00,  1.10677423e+01,  3.68959641e+00,
          3.47960925e+00, -2.99634427e-01,  6.79832125e+00,
         -4.26959467e+00,  3.07012057e+00,  7.96007776e+00,
          1.69290333e+01, -1.52800207e+01, -7.43998480e+00,
         -1.01226568e+01,  2.17852859e+01,  2.56065416e+00,
         -1.68843460e+00, -1.64956582e+00, -5.11790705e+00],
        [ 3.53472400e+00,  7.11240053e+00, -7.46044970e+00,
          5.93153620e+00,  7.90499878e+00,  8.98063660e+00,
         -8.18702602e+00,  2.26997924e+00, -9.92850304e+00,
          9.51546288

In [ ]:
frame.render()

In [63]:
frame.extract()

starting xshear calculations in 100 processes


In [5]:
df = render.DrawField(5000, catalog, band="i")
df.prepare()
df.make_infodicts()
df.multi_render(100)
df.collate_stamps()

starting xshear calculations in 100 processes


In [6]:
noise_std = 8.36335 
noise = np.random.normal(scale=noise_std, size=(5000, 5000))

In [7]:
arr = df.canvas.array + noise
#arr = arr[2100:2900, 2100:2900]
fio.write("test.fits", arr, clobber=True)